In [1]:
#General purpose: 
import matplotlib.pyplot as plt
import numpy
import numpy as np
from mpl_toolkits.mplot3d import Axes3D

import pandas as pd

#PROSPECT+SAIL Radiative transfer mode package
import prosail

#Sampling design package
import lhsmdu

#package to for operations on spectral data
import pysptools as sptool 
from pysptools import distance
#machine learning packages are imported later, nearer to the model

# First we create datasets of 10 000 simulated spectra

### Varying parameters: Cab, Car, Cw, Cm and LAI

In [2]:
#number of samples
train_n10000 = 10000


n_traits=5 #I will test on 5 varying traits: cab, car, cw,cm,lai

#generating a LHS hypercube (it uses a 0 to 1 interval that can be used as a multiplier against the different traits)
np.random.seed(0)
LHS_train10000 = lhsmdu.createRandomStandardUniformMatrix(n_traits,train_n10000 ) #the package has a more advanced method but it is too slow to process


#max_n=1 #this value should go from 1 to 2, so i make it change from 0 to 1 here and then add 1 later
max_cab=79. #add 1
max_car=9. #add 1
#max_cbrown= 9.99 #add 0.01
max_cw=199 #add 1
max_cm=199 #add 1
max_lai = 9.9 #add 0.1

# The next 2 snippets are functions needed for generating the data at sentinel resolution

### First a function for better control of the prosail call

In [18]:
#in here I create a custom call for prosail, this allows me to more easily control the default values
def custom_prosail(cab,car, cw,cm,lai):
    import prosail
    #default parameters
    n= 1.2
    cbrown=0.0
    typelidf=1
    lidfa = -1 #leaf angle distribution parameter a and b (Spherical)
    lidfb=0
    hspot= 0.01 #hotspot parameters
    #sun and viewing angle
    tts=30. #observation and solar position parameters 27
    tto=10. 
    psi=0. #74
    rho_out = prosail.run_prosail(n,
                                 cab,
                                 car,
                                 cbrown,
                                 cw,
                                 cm,
                                 lai,
                                 lidfa,hspot,tts,tto,psi,
                                 typelidf, lidfb,
                                 factor='DHR', psoil=1.)
    return(rho_out)

  

### Then a function to convert the input hyperspectral data to Sentinel 2A data using a weighted mean approach

In [4]:
#this function also transforms the hyperspectral data to sentinel data
def Prosail2S2(path2csv, spectra_input):
    #importing pandas
    import pandas as pd
    import numpy
    import numpy as np
    
    s2_table = pd.read_csv(path2csv,sep=";",decimal=",") #check if this is proper, regarding the sep and dec
    s2_table_sel = s2_table[s2_table['SR_WL'].between(400,2500)] #selects all values between 400 and 2500
    spectra_input_df = pd.DataFrame(data=spectra_input,columns=["rho"],index=s2_table_sel.index) #transforms the input array into a pandas df with the column name rho and row.index = to the original input table

  
    rho_s2 = s2_table_sel.multiply(spectra_input_df['rho'],axis="index") #calculates the numerator
    w_band_sum = s2_table_sel.sum(axis=0,skipna = True) #calculates the denominator

    output = (rho_s2.sum(axis=0)/w_band_sum).rename_axis("ID").values #runs the weighted mean and converts the output to a numpy array

    return output[1:] #removes the first value because it represents the wavelength column

#please LOAD THTE FILE NOW
filepath="/Users/BSibiya/Desktop/Sandberg Fynbos Reserve/S2_response.csv"


### Now we create a function that generates the data given the n input samples

In [5]:
#function expects as input a PD dataframe with the columns properly named
#notice if you change any defaults on the custom_prosail function then you have to go back and
#change that
#this function also transforms the hyperspectral data to sentinel data
def Gen_spectra_data(traits):
    k = 1
    #pd_train_traits=traits
    #print(range(len(traits)))
    for i in range(len(traits)):
        #n_t = pd_train_traits["n"][i]
        cab_t = traits["cab"][i]
        car_t = traits["car"][i]
        #cbrown_t = pd_train_traits["cbrown"][i]
        cw_t = traits["cw"][i]
        cm_t = traits["cm"][i]
        lai_t = traits["lai"][i]
    
        if k == 1:
            tr_rho_s = custom_prosail(cab_t,car_t,cw_t,cm_t,lai_t)
            tr_rho_s = Prosail2S2(filepath,tr_rho_s)
            #plt.plot ( x, tr_rho_s, ':', label="Training prosail")
            #plt.legend(loc='best')
    
        if k > 1:
            tr_rho_t = custom_prosail(cab_t,car_t,cw_t,cm_t,lai_t)
            tr_rho_t = Prosail2S2(filepath,tr_rho_t)
            tr_rho_s = np.vstack((tr_rho_s,tr_rho_t))
            #plt.plot ( x, tr_rho_t, ':')
        
        k = k+1
    
    rho_samples=tr_rho_s
    
    return rho_samples


### Now we can get the datasets

In [6]:
#preparing function inputs

pd_traits10000 = pd.DataFrame.transpose(pd.DataFrame(LHS_train10000))

pd_traits10000.columns = ["cab","car","cw","cm","lai"]

pd_traits10000["cab"]=pd_traits10000["cab"]*max_cab+1.
pd_traits10000["car"]=pd_traits10000["car"]*max_car+1. 
pd_traits10000["cw"] =pd_traits10000["cw"] *max_cw+1.
pd_traits10000["cm"] =pd_traits10000["cm"] *max_cm+1.
pd_traits10000["lai"]=pd_traits10000["lai"]*max_lai+.1

In [7]:
pd_traits10000

cab       car          cw          cm       lai
0     44.356267  7.734412   79.042419  151.866958  3.755638
1     57.499960  2.621824    9.190161  101.160384  2.192127
2     48.618307  4.501208  184.736813   36.226316  4.821357
3     44.045771  1.338402   81.840760  166.674765  0.914120
4     34.468729  1.106090  188.912154  103.848131  2.452828
...         ...       ...         ...         ...       ...
9995  44.485299  7.733571  124.849480  134.008236  5.508655
9996  32.374955  3.684400  106.696947  198.987383  6.963773
9997  60.915932  5.018102  170.727933  118.056552  2.413381
9998   2.879207  4.241140  147.111681   85.498367  8.326146
9999  65.272431  6.632980  128.160486  180.424906  5.558047

[10000 rows x 5 columns]

In [8]:
#pd_train_traits["n"]=pd_t

np_spectra10000 = Gen_spectra_data(pd_traits10000)

C:\ProgramData\Anaconda3\envs\pedro\lib\site-packages\prosail\prospect_d.py:150: RuntimeWarning: divide by zero encountered in divide
  b       = (1-rq+tq+D)/(2*t)
C:\ProgramData\Anaconda3\envs\pedro\lib\site-packages\prosail\prospect_d.py:150: RuntimeWarning: overflow encountered in divide
  b       = (1-rq+tq+D)/(2*t)
C:\ProgramData\Anaconda3\envs\pedro\lib\site-packages\prosail\prospect_d.py:156: RuntimeWarning: invalid value encountered in divide
  Rsub    = a*(bN2-1)/denom
C:\ProgramData\Anaconda3\envs\pedro\lib\site-packages\prosail\prospect_d.py:157: RuntimeWarning: invalid value encountered in divide
  Tsub    = bNm1*(a2-1)/denom
C:\ProgramData\Anaconda3\envs\pedro\lib\site-packages\prosail\prospect_d.py:150: RuntimeWarning: divide by zero encountered in divide
  b       = (1-rq+tq+D)/(2*t)
C:\ProgramData\Anaconda3\envs\pedro\lib\site-packages\prosail\prospect_d.py:150: RuntimeWarning: overflow encountered in divide
  b       = (1-rq+tq+D)/(2*t)
C:\ProgramData\Anaconda3\envs\pe

In [9]:
print(np_spectra10000.shape)

(10000, 13)


In [11]:
np_traits10000 = pd_traits10000.iloc[:,:].values

In [12]:
np_traits10000

array([[ 44.35626681,   7.73441183,  79.04241931, 151.86695779,
          3.75563761],
       [ 57.49995994,   2.62182437,   9.19016065, 101.16038376,
          2.19212743],
       [ 48.61830671,   4.5012083 , 184.73681314,  36.22631596,
          4.82135721],
       ...,
       [ 60.91593214,   5.01810184, 170.72793346, 118.05655205,
          2.41338136],
       [  2.87920677,   4.24113952, 147.11168134,  85.49836656,
          8.32614641],
       [ 65.27243132,   6.63297981, 128.16048573, 180.4249064 ,
          5.55804678]])

In [13]:

pd_traits10000 = pd.DataFrame(np_traits10000)

In [14]:
pd_traits10000.columns = ["cab","car","cw","cm","lai"]

In [15]:
pd_traits10000

cab       car          cw          cm       lai
0     44.356267  7.734412   79.042419  151.866958  3.755638
1     57.499960  2.621824    9.190161  101.160384  2.192127
2     48.618307  4.501208  184.736813   36.226316  4.821357
3     44.045771  1.338402   81.840760  166.674765  0.914120
4     34.468729  1.106090  188.912154  103.848131  2.452828
...         ...       ...         ...         ...       ...
9995  44.485299  7.733571  124.849480  134.008236  5.508655
9996  32.374955  3.684400  106.696947  198.987383  6.963773
9997  60.915932  5.018102  170.727933  118.056552  2.413381
9998   2.879207  4.241140  147.111681   85.498367  8.326146
9999  65.272431  6.632980  128.160486  180.424906  5.558047

[10000 rows x 5 columns]

In [16]:
train_df_10000 = np_spectra10000[:,[0, 1,2,3,4,5,6,7, 8, 9, 10,11, 12]]

In [17]:
pd.DataFrame(train_df_10000)

0         1         2         3         4         5         6   \
0     0.000020  0.021888  0.018678  0.021177  0.019121  0.022723  0.022855   
1     0.013377  0.035319  0.034352  0.040146  0.039568  0.044237  0.045654   
2     0.022744  0.020078  0.016566  0.018621  0.016366  0.019825  0.019783   
3     0.000000  0.091321  0.099860  0.119442  0.125000  0.134173  0.140956   
4     0.011950  0.031097  0.029425  0.034183  0.033141  0.037474  0.038487   
...        ...       ...       ...       ...       ...       ...       ...   
9995  0.001421  0.019678  0.016099  0.018055  0.015756  0.019183  0.019103   
9996  0.000000  0.018432  0.015791  0.017683  0.015355  0.018761  0.018655   
9997  0.006810  0.031655  0.030077  0.034971  0.033991  0.038368  0.039435   
9998  0.011634  0.019367  0.015737  0.017617  0.015284  0.018686  0.018576   
9999  0.000000  0.019432  0.016077  0.018029  0.015729  0.019154  0.019072   

            7         8         9             10        11   12  
0     0.022604  0.022469  0.022093  1.014454e-02  0.000000  0.0  
1     0.046805  0.047500  0.048973  5.078936e-02  0.050214  0.0  
2     0.019344  0.019097  0.018472  3.588022e-03  0.000000  0.0  
3     0.147948  0.152105  0.161278  6.525422e-02  0.000000  0.0  
4     0.039197  0.039632  0.040523  1.098618e-06  0.000000  0.0  
...        ...       ...       ...           ...       ...  ...  
9995  0.018622  0.018350  0.017670  2.042952e-04  0.000000  0.0  
9996  0.018147  0.017859  0.017142  2.784577e-07  0.000000  0.0  
9997  0.040204  0.040673  0.041641  1.395311e-06  0.000000  0.0  
9998  0.018063  0.017772  0.017049  3.222116e-03  0.000000  0.0  
9999  0.018589  0.018317  0.017633  2.304764e-07  0.000000  0.0  

[10000 rows x 13 columns]

### Now we need to K-fold the data so we can do the LOOCV - Leave one out cross validation

In [86]:
from sklearn.model_selection import KFold # import KFol

#this command is enough to set u the k-fold
kf = KFold(n_splits=5) # Define the split 

#test spot
#X = np_spectra0500
#Y = np.arange(len(np_spectra0500)) #this is simply a place holder

#The kfold of sklearn doesn't actually randomize the folding but that is ok because
#the samples were generated randomly anyway. 
#k = 1
#for train_index, test_index in kf.split(X):
  #print("TRAIN:", train_index, "TEST:", test_index)
  #X_train, X_test = X[train_index], X[test_index]
  #y_train, y_test = Y[train_index], Y[test_index]
  #print(k)
  #print(train_index.shape)
  #print(test_index.shape)
  #k=k+1
#uncomment above to see how it works


#### Now we set up all the machine learning models

In [92]:
#machine learning stuff

#NEURAL NETWORK - Keras will be updated soon so this colab will also have to be changed
from sklearn.neural_network import MLPRegressor as ANN_reg #this is a simpler neural network package
from keras.models import Sequential
from keras.layers import Dense
import tensorflow.compat.v1 as tf
tf.disable_v2_behavior()
#ignore the warning for now

#Random FOREST
# Fitting Random Forest Regression to the dataset 
# import the regressor 
from sklearn.ensemble import RandomForestRegressor 

#Gaussian processes
from sklearn.gaussian_process import GaussianProcessRegressor
from sklearn.gaussian_process.kernels import ConstantKernel, Matern

#initializing the ANN
ann_ml = Sequential()
#ann_ml.add(Dense(9, input_dim=9, activation='linear'))
ann_ml.add(Dense(10, input_dim=9, activation='tanh'))
ann_ml.add(Dense(6, activation='relu'))
ann_ml.add(Dense(4)) #indeed this ha to be added in this case without any activ function, the R script added this on its own
#model.add(Dense(1, activation='sigmoid'))

# compile the keras model
ann_ml.compile(loss='mean_squared_error', optimizer='adam', metrics=['accuracy'])

#initializing the random forest
rfr_ml = RandomForestRegressor(n_estimators=1000,random_state=0,
                              min_samples_leaf=5,min_samples_split=5,verbose=1)
#initializing the gaussian process
gpr_ml = GaussianProcessRegressor(n_restarts_optimizer=50,
                                        normalize_y=True,
                                        random_state=0)


#### Creating an empty pandas dataframe to store the output of the models

In [88]:
column_names=["Model",
              "NSamples",
              "Variable",
              "Fold_nr",
              "ExplVar",
              "Max_err",
              "Mean_abs_Err",
              "Mean_sqr_err",
              #"Mean_sqr_lg_err",
              "Median_abs_err",
              "r2",
              "MAPE"]
              #"Mean_poiss_dev",
              #"Mean_gamma_dev"]
              #"Mean_tweed_dev"]

#mape is not existant in the package so we have to create it:
#https://stats.stackexchange.com/questions/58391/mean-absolute-percentage-error-mape-in-scikit-learn
#from sklearn.utils import check_array
def mean_absolute_percentage_error(y_true, y_pred): 
    ## Note: does not handle mix 1d representation
    #if _is_1d(y_true): 
    #    y_true, y_pred = _check_1d_array(y_true, y_pred)
    return np.mean(np.abs((y_true - y_pred) / y_true)) * 100

In [89]:
#creating a df to receive the data
df_metrics = pd.DataFrame(columns=column_names)

#we pick only the bands at 20m resolution - i reckon it is actually peaceful to use everything.. 

#first we subset the bands to the 20m resolution only
#S2A_SR_AV_B1	S2A_SR_AV_B2	S2A_SR_AV_B3	
#S2A_SR_AV_B4	S2A_SR_AV_B5	S2A_SR_AV_B6	
#S2A_SR_AV_B7	S2A_SR_AV_B8	S2A_SR_AV_B8A	
#S2A_SR_AV_B9	S2A_SR_AV_B10	S2A_SR_AV_B11	
#S2A_SR_AV_B12

train_df_10000 = np_spectra10000[:,[1,2,3,4,5,6,8,11,12]]



#importing metric functions
from sklearn import metrics

#the ANN requires that we transform the variables
from sklearn.preprocessing import MinMaxScaler 
scaler_10000 = MinMaxScaler()

### Measuring the accuraccy the of the regression

In [97]:
#with 10000 samples
k=1
for train_index, test_index in kf.split(train_df_10000):

    #subsetting for ith k-fold
    X_train, X_test = train_df_10000[train_index], train_df_10000[test_index]
    Y_train, Y_test = np_traits10000[train_index], np_traits10000[test_index]
    label_names = ["cab","car","cw","cm","lai"]

    #ANN - Training 
    scaler_10000.fit(Y_train)
    Y_train_norm = scaler_10000.transform(Y_train)
    #ann_ml.fit(X_train,Y_train_norm,epochs=1500,verbose=0)

    #RF - Training n
    rfr_ml.fit(X_train,Y_train)

    #GPR - Training 
    gpr_ml.fit(X_train,Y_train)

    #Prediction
    #y_ann_10000 = scaler_10000.inverse_transform(ann_ml.predict(X_test))
    y_rfr_10000 = rfr_ml.predict(X_test)
    y_gpr_10000 = gpr_ml.predict(X_test)
    


    for i in range(n_traits):

        rfr_temp_list = {"Model":"RFr",
                         "NSamples":10000,
                         "Variable":label_names[i],
                         "Fold_nr":k,
                         "ExplVar": metrics.explained_variance_score(Y_test[:,i], y_rfr_10000[:,i]),
                         "Max_err": metrics.max_error(Y_test[:,i], y_rfr_10000[:,i]),
                         "Mean_abs_Err": metrics.mean_absolute_error(Y_test[:,i], y_rfr_10000[:,i]),
                         "Mean_sqr_err": metrics.mean_squared_error(Y_test[:,i], y_rfr_10000[:,i]),
                         #"Mean_sqr_lg_err": metrics.mean_squared_log_error(Y_test[:,i], y_rfr_0500[:,i]),
                         "Median_abs_err" : metrics.median_absolute_error(Y_test[:,i], y_rfr_10000[:,i]),
                         "r2": metrics.r2_score(Y_test[:,i], y_rfr_10000[:,i]),
                         #"Mean_poiss_dev" : metrics.mean_poisson_deviance(Y_test[:,i], y_rfr_0500[:,i]),
                         #"Mean_gamma_dev" : metrics.mean_gamma_deviance(Y_test[:,i], y_rfr_0500[:,i])}
                         #"Mean_tweed_dev" : metrics.mean_tweedie_deviance(Y_test[:,i], y_rfr_0500[:,i])}
                         "MAPE": mean_absolute_percentage_error(Y_test[:,i], y_rfr_10000[:,i])}

        gpr_temp_list = {"Model":"GPR",
                         "NSamples":10000,
                         "Variable":label_names[i],
                         "Fold_nr":k,
                         "ExplVar": metrics.explained_variance_score(Y_test[:,i], y_gpr_10000[:,i]),
                         "Max_err": metrics.max_error(Y_test[:,i], y_gpr_10000[:,i]),
                         "Mean_abs_Err": metrics.mean_absolute_error(Y_test[:,i], y_gpr_10000[:,i]),
                         "Mean_sqr_err": metrics.mean_squared_error(Y_test[:,i], y_gpr_10000[:,i]),
                         #"Mean_sqr_lg_err": metrics.mean_squared_log_error(Y_test[:,i], y_gpr_0500[:,i]),
                         "Median_abs_err" : metrics.median_absolute_error(Y_test[:,i], y_gpr_10000[:,i]),
                         "r2": metrics.r2_score(Y_test[:,i], y_gpr_10000[:,i]),
                         #"Mean_poiss_dev" : metrics.mean_poisson_deviance(Y_test[:,i], y_gpr_0500[:,i]),
                         #"Mean_gamma_dev" : metrics.mean_gamma_deviance(Y_test[:,i], y_gpr_0500[:,i])}
                         #"Mean_tweed_dev" : metrics.mean_tweedie_deviance(Y_test[:,i], y_gpr_0500[:,i])}
                         "MAPE": mean_absolute_percentage_error(Y_test[:,i], y_gpr_10000[:,i])}

        #appending to the dataframe
        #df_metrics = df_metrics.append(ann_temp_list,ignore_index=True)
        df_metrics = df_metrics.append(rfr_temp_list,ignore_index=True)
        df_metrics = df_metrics.append(gpr_temp_list,ignore_index=True)
    k = k+1

df_metrics.to_csv("run0500.csv",sep=";",decimal=",")


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done 1000 out of 1000 | elapsed:  1.7min finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done 1000 out of 1000 | elapsed:    0.4s finished
C:\Users\BSibiya\AppData\Local\Temp\ipykernel_2120\2830482603.py:64: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_metrics = df_metrics.append(rfr_temp_list,ignore_index=True)
C:\Users\BSibiya\AppData\Local\Temp\ipykernel_2120\2830482603.py:65: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_metrics = df_metrics.append(gpr_temp_list,ignore_index=True)
C:\Users\BSibiya\AppData\Local\Temp\ipykernel_2120\2830482603.py:64: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a

In [98]:
df_metrics

Model NSamples Variable Fold_nr   ExplVar     Max_err  Mean_abs_Err  \
0    RFr    10000      cab       1 -0.032815   50.868851     20.441474   
1    GPR    10000      cab       1 -0.001177   44.461886     20.297528   
2    RFr    10000      car       1 -0.065414    5.714222      2.291406   
3    GPR    10000      car       1 -0.009571    4.884533      2.252521   
4    RFr    10000       cw       1  0.348108  145.164668     37.893331   
5    GPR    10000       cw       1  0.374217  118.359905     37.624300   
6    RFr    10000       cm       1  0.495915  123.545475     32.087092   
7    GPR    10000       cm       1  0.481988  109.559476     34.742594   
8    RFr    10000      lai       1  0.997167    1.533171      0.055726   
9    GPR    10000      lai       1  0.808301    4.919528      1.034540   
10   RFr    10000      cab       2 -0.036501   56.259101     19.730842   
11   GPR    10000      cab       2 -0.002103   41.572707     19.618133   
12   RFr    10000      car       2 -0.039875    6.268645      2.274327   
13   GPR    10000      car       2 -0.014151   10.396650      2.261522   
14   RFr    10000       cw       2  0.345918  140.967200     37.156314   
15   GPR    10000       cw       2  0.370709  123.783120     37.000505   
16   RFr    10000       cm       2  0.451620  164.806177     32.575162   
17   GPR    10000       cm       2  0.481731  102.647983     34.293068   
18   RFr    10000      lai       2  0.995543    3.407220      0.065388   
19   GPR    10000      lai       2  0.820282    2.942156      1.028786   
20   RFr    10000      cab       3 -0.074169   55.210437     20.024672   
21   GPR    10000      cab       3 -0.019401  129.974175     19.616957   
22   RFr    10000      car       3 -0.040033    6.101031      2.276363   
23   GPR    10000      car       3 -0.014686   10.864162      2.259237   
24   RFr    10000       cw       3  0.389158  136.936498     36.282930   
25   GPR    10000       cw       3  0.401336  207.079078     36.335810   
26   RFr    10000       cm       3  0.449105  136.888470     33.581241   
27   GPR    10000       cm       3  0.436336  406.503733     35.372701   
28   RFr    10000      lai       3  0.994640    3.638722      0.064262   
29   GPR    10000      lai       3  0.782310   23.507073      1.044637   
30   RFr    10000      cab       4 -0.049519   56.697492     20.107019   
31   GPR    10000      cab       4 -0.020949  106.921989     19.960152   
32   RFr    10000      car       4 -0.033858    5.908060      2.306886   
33   GPR    10000      car       4 -0.006544    7.288101      2.298999   
34   RFr    10000       cw       4  0.368963  158.264668     36.582437   
35   GPR    10000       cw       4  0.388175  152.573857     36.745911   
36   RFr    10000       cm       4  0.475442  127.372103     32.940625   
37   GPR    10000       cm       4  0.462842  232.784722     35.428000   
38   RFr    10000      lai       4  0.997536    1.704156      0.051518   
39   GPR    10000      lai       4  0.800863    9.636246      1.055315   
40   RFr    10000      cab       5 -0.056451   51.020245     20.120569   
41   GPR    10000      cab       5 -0.053588  230.540678     19.850681   
42   RFr    10000      car       5 -0.051448    6.087761      2.366844   
43   GPR    10000      car       5 -0.057163   21.179362      2.353185   
44   RFr    10000       cw       5  0.350564  133.353293     36.736684   
45   GPR    10000       cw       5  0.378515  145.628031     36.781397   
46   RFr    10000       cm       5  0.515193  150.681571     30.815110   
47   GPR    10000       cm       5  0.505608  166.886185     33.380755   
48   RFr    10000      lai       5  0.996266    1.726429      0.059434   
49   GPR    10000      lai       5  0.804450    4.833612      1.049738   

    Mean_sqr_err  Median_abs_err        r2        MAPE  
0     561.446752       20.030593 -0.034375  155.009328  
1     543.901579       20.099842 -0.002051  155.815873  
2       7.136541        2.228414 -0.065590   68.675945  
